In [1]:
import pandas as pd
import numpy as np
import requests
import time
import matplotlib.pyplot as plt
%matplotlib inline
import seaborn as sns
from pandas import datetime
import datedelta
import plotly
plotly.tools.set_credentials_file(username='sasi_ynwa', api_key='wEm5TtVT8TOVKzFyd8CA')
import plotly.graph_objs as go
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
init_notebook_mode(connected=True)

In [14]:
w = requests.get(url='https://poloniex.com/public?command=returnChartData&currencyPair=USDT_XRP&end=9999999999&period=86400&start=1405699200')

In [15]:
dfXRP = pd.DataFrame.from_records(w.json())

In [16]:
start =time.time()#works but first create a column wiht DateTime
dfXRP['DateTime'] = pd.Series(np.random.randn(len(dfXRP)), index=dfXRP.index)
for i, row in dfXRP.iterrows():
    dfXRP['DateTime'][i] = datetime.fromtimestamp(row['date']).strftime("%m-%d-%Y %H:%M:%S")
dfXRP['DateTime'] =  pd.to_datetime(dfXRP['DateTime'], format='%m-%d-%Y %H:%M:%S')
end = time.time()
print(end - start)

C:\Users\msasi\Anaconda3\lib\site-packages\ipykernel_launcher.py:4: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy

C:\Users\msasi\Anaconda3\lib\site-packages\pandas\core\indexing.py:179: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy



55.90994048118591


In [17]:
#Using Roller to generate Moving Averages(Simple). Here we re multiplying by 6 cos each day has 6 recordings
roller = dfXRP['close'].rolling(10*6)
dfXRP['10DayMA'] = roller.mean()

roller = dfXRP['close'].rolling(30*6)
dfXRP['30DayMA'] = roller.mean()

roller = dfXRP['close'].rolling(50*6)
dfXRP['50DayMA'] = roller.mean()

In [22]:
data = [
    go.Scatter(
        x=dfXRP['DateTime'], # assign x as the dataframe column 'x'
        y=dfXRP['close'],
        name = 'Closing Price'
    ),
    go.Scatter(
        x = dfXRP['DateTime'],
        y = dfXRP['50DayMA'],
        name = '50DayMA'
    ),
    go.Scatter(
        x = dfXRP['DateTime'],
        y = dfXRP['30DayMA'],
        name = '30DayMA'
    ),
    go.Scatter(
        x = dfXRP['DateTime'],
        y = dfXRP['10DayMA'],
        name = '10DayMA'
    ),
   # go.Scatter(
    #    x = dfXRP['DateTime'],
     #   y = dfXRP['weightedAverage'],
      #  name = 'Weighted Average Price'
    #)#,
   # go.Candlestick(x=dfXRP.DateTime,
    #                   open=dfXRP.open,
     #                  high=dfXRP.high,
      #                 low=dfXRP.low,
       #                close=dfXRP.close,
        #               increasing=dict(line=dict(color= '#00ff00')),
         #              decreasing=dict(line=dict(color= '#FF0000')))
]
# IPython notebook
plotly.offline.iplot(data)

In [7]:
#Using Roller to generate Moving Averages(Simple) for Volume
roller = dfXRP['volume'].rolling(10*6)
dfXRP['Vol10DayMA'] = roller.mean()

roller = dfXRP['volume'].rolling(30*6)
dfXRP['Vol30DayMA'] = roller.mean()

roller = dfXRP['volume'].rolling(50*6)
dfXRP['Vol50DayMA'] = roller.mean()

In [8]:
data = [
    go.Scatter(
        x=dfXRP['DateTime'], # assign x as the dataframe column 'x'
        y=dfXRP['volume'],
        name = 'Volume'
    ),
    go.Scatter(
        x = dfXRP['DateTime'],
        y = dfXRP['Vol50DayMA'],
        name = '50DayMA - Volume'
    ),
    go.Scatter(
        x = dfXRP['DateTime'],
        y = dfXRP['Vol30DayMA'],
        name = '30DayMA - Volume'
    ),
    go.Scatter(
        x = dfXRP['DateTime'],
        y = dfXRP['Vol10DayMA'],
        name = '10DayMA - Volume'
    )#,
    #go.Candlestick(x=dfETH.DateTime,
     #                  open=dfETH.open,
      #                 high=dfETH.high,
       #                low=dfETH.low,
        #               close=dfETH.close,
         #              increasing=dict(line=dict(color= '#17BECF')),
          #             decreasing=dict(line=dict(color= '#7F7F7F')))
]
# IPython notebook
plotly.offline.iplot(data)

In [9]:
#New try, Volatility window is for 3 days shift should be done -1 since we are comparing results with 1 up 

dfXRP['Returns'] = ((dfXRP['close'] / dfXRP['close'].shift(-1)) - 1)
dfXRP['Volatility'] = pd.rolling_std(dfXRP['Returns'], window=18)

C:\Users\msasi\Anaconda3\lib\site-packages\ipykernel_launcher.py:4: FutureWarning:

pd.rolling_std is deprecated for Series and will be removed in a future version, replace with 
	Series.rolling(window=18,center=False).std()



In [10]:
#Using Roller to generate Moving Averages(Simple) for Volatility
roller = dfXRP['Volatility'].rolling(10*6)
dfXRP['Volatility10DayMA'] = roller.mean()

roller = dfXRP['Volatility'].rolling(30*6)
dfXRP['Volatility30DayMA'] = roller.mean()

roller = dfXRP['Volatility'].rolling(50*6)
dfXRP['Volatility50DayMA'] = roller.mean()

In [11]:
dfXRP['meanLineVolatility'] = dfXRP['Volatility'].mean()

In [13]:
data = [
    go.Scatter(
        x=dfXRP['DateTime'], # assign x as the dataframe column 'x'
        y=dfXRP['Volatility'],
        name = 'Volatility'
    ),
     go.Scatter(
        x=dfXRP['DateTime'], # assign x as the dataframe column 'x'
        y=dfXRP['meanLineVolatility'],
        name = 'Volatility mean Line'
    ),
    go.Scatter(
        x = dfXRP['DateTime'],
        y = dfXRP['Volatility10DayMA'],
        name = '10DayMA - Volatility'
    ),
    go.Scatter(
        x = dfXRP['DateTime'],
        y = dfXRP['Volatility30DayMA'],
        name = '30DayMA - Volatility'
    )#,
   # go.Scatter(
    #    x = dfXRP['DateTime'],
     #   y = dfXRP['Volatility50DayMA'],
      #  name = '50DayMA - Volatility'
    #)#,
    #go.Candlestick(x=dfETH.DateTime,
     #                  open=dfETH.open,
      #                 high=dfETH.high,
       #                low=dfETH.low,
        #               close=dfETH.close,
         #              increasing=dict(line=dict(color= '#17BECF')),
          #             decreasing=dict(line=dict(color= '#7F7F7F')))
]
# IPython notebook
plotly.offline.iplot(data)

In [23]:
roller = dfXRP['close'].rolling(3*6)
dfXRP['3DayMA'] = roller.mean()

roller = dfXRP['close'].rolling(5*6)
dfXRP['5DayMA'] = roller.mean()

roller = dfXRP['close'].rolling(10*6)
dfXRP['10DayMA'] = roller.mean()

In [24]:
data = [
    go.Scatter(
        x=dfXRP['DateTime'], # assign x as the dataframe column 'x'
        y=dfXRP['close'],
        name = 'Closing Price'
    ),
    go.Scatter(
        x = dfXRP['DateTime'],
        y = dfXRP['5DayMA'],
        name = '5DayMA'
    ),
    go.Scatter(
        x = dfXRP['DateTime'],
        y = dfXRP['3DayMA'],
        name = '3DayMA'
    ),
    go.Scatter(
        x = dfXRP['DateTime'],
        y = dfXRP['10DayMA'],
        name = '10DayMA'
    ),
   # go.Scatter(
    #    x = dfXRP['DateTime'],
     #   y = dfXRP['weightedAverage'],
      #  name = 'Weighted Average Price'
    #)#,
   # go.Candlestick(x=dfXRP.DateTime,
    #                   open=dfXRP.open,
     #                  high=dfXRP.high,
      #                 low=dfXRP.low,
       #                close=dfXRP.close,
        #               increasing=dict(line=dict(color= '#00ff00')),
         #              decreasing=dict(line=dict(color= '#FF0000')))
]
# IPython notebook
plotly.offline.iplot(data)